In [1]:
import requests
import pandas as pd
import numpy as np

http_proxy  = "http://proxy-web.micron.com:80"
https_proxy = "http://proxy-web.micron.com:80"
proxyDict = { 
    "http":http_proxy, 
    "https":https_proxy              
}

pd.set_option('display.max_rows', None) #show every row for pandas
pd.set_option('display.max_columns', None) #show every column for pandas

g_year = 108
g_season = 1
g_how_many_year = 3

In [2]:
# sii:上市, otc:上櫃
# TWSE之數據是至該季的累計數據而非單季數據, EX: Q3=> TWSE: Q1~Q3, 財報狗:Q3
def financial_statement(year, season, stocktype, type='綜合損益彙總表'):
    if year >= 1000:
        year -= 1911
        
    if type == '綜合損益彙總表':
        url = 'https://mops.twse.com.tw/mops/web/ajax_t163sb04'
    elif type == '資產負債彙總表':
        url = 'https://mops.twse.com.tw/mops/web/ajax_t163sb05'
    elif type == '營益分析彙總表':
        url = 'https://mops.twse.com.tw/mops/web/ajax_t163sb06'
    else:
        print('type does not match')
    
    r = requests.post(url, {
        'encodeURIComponent':1,
        'step':1,
        'firstin':1,
        'off':1,
        'TYPEK':stocktype,
        'year':str(year),
        'season':str(season),
    }, stream=True)#, verify=False, proxies=proxyDict)
    
    r.encoding = 'utf8'
    dfs = pd.read_html(r.text)
    
    
    for i, df in enumerate(dfs):
        df.columns = df.iloc[0]
        dfs[i] = df.iloc[1:]
        
    df = pd.concat(dfs).applymap(lambda x: x if x != '--' else np.nan)
    df = df[df[u'公司代號'] != u'公司代號']
    df = df[~df[u'公司代號'].isnull()]
    
    #http://pandas.pydata.org/pandas-docs/stable/generated/pandas.DataFrame.add_suffix.html
    #http://pandas.pydata.org/pandas-docs/stable/generated/pandas.DataFrame.add_prefix.html
    suffix_format = "_{0}Q{1}".format(year, season)
    
    #return df.add_suffix(suffix_format)
    return df

In [3]:
def generate_df_for_stocktype(year, season, howmany_year_data, stocktype, title_name, with_col_name, sheettype):
    df = financial_statement(year, season, stocktype, type=sheettype)[[u'公司代號',u'公司名稱',with_col_name]]
    df.rename(columns = {df.columns[2]: '{0}_{1}Q{2}'.format(title_name, year, season)}, inplace = True)

    for i in range(howmany_year_data*4):
        # calculate previous quarter data 107Q1 => we want the previous data is 106Q4 AND then 106Q3, 106Q2, 106Q1, 105Q4
        if (season != 1):
            season = season - 1
        else:
            season = 4
            year = year - 1
        #https://pandas.pydata.org/pandas-docs/stable/generated/pandas.DataFrame.merge.html
        dfanother = financial_statement(year, season, stocktype, type=sheettype)[[u'公司代號',with_col_name]]    
        print(dfanother.columns[1])

        dfanother.rename(columns = {dfanother.columns[1]: '{0}_{1}Q{2}'.format(title_name, year, season)}, inplace = True)

        df = df.merge(dfanother, on=u'公司代號', how='inner')
        print("year:", year)
        #print("year: {0}".format(year))
        print("season:", season)
        #print("season: {0}".format(season))

    return df

In [4]:
df_revenue_sii = generate_df_for_stocktype(g_year, g_season, g_how_many_year, 'sii', 'Revenue', u'營業收入', '綜合損益彙總表')

df_revenue_sii

C:\ProgramData\Anaconda2\lib\site-packages\ipykernel_launcher.py:34: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.



營業收入
('year:', 107)
('season:', 4)
營業收入
('year:', 107)
('season:', 3)
營業收入
('year:', 107)
('season:', 2)
營業收入
('year:', 107)
('season:', 1)
營業收入
('year:', 106)
('season:', 4)
營業收入
('year:', 106)
('season:', 3)
營業收入
('year:', 106)
('season:', 2)
營業收入
('year:', 106)
('season:', 1)
營業收入
('year:', 105)
('season:', 4)
營業收入
('year:', 105)
('season:', 3)
營業收入
('year:', 105)
('season:', 2)
營業收入
('year:', 105)
('season:', 1)


公司代號      公司名稱 Revenue_108Q1 Revenue_107Q4 Revenue_107Q3 Revenue_107Q2  \
0    2801      彰化銀行           NaN           NaN           NaN           NaN   
1    2809      京城銀行           NaN           NaN           NaN           NaN   
2    2812      台中銀行           NaN           NaN           NaN           NaN   
3    2820        華票           NaN           NaN           NaN           NaN   
4    2834      臺灣企銀           NaN           NaN           NaN           NaN   
5    2836        高銀           NaN           NaN           NaN           NaN   
6    2838      聯邦銀行           NaN           NaN           NaN           NaN   
7    2845      遠東商銀           NaN           NaN           NaN           NaN   
8    2849      安泰銀行           NaN           NaN           NaN           NaN   
9    2855      統一證券           NaN           NaN           NaN           NaN   
10   6005       群益證           NaN           NaN           NaN           NaN   
11   6024       群益期           NaN           NaN           NaN           NaN   
12   1101        台泥      25356328     124594602      89657354      57500246   
13   1102        亞泥      19385675      82741004      60908065      39009089   
14   1103        嘉泥        452376       2092406       1495207       1000927   
15   1104      環球水泥       1187296       4780994       3436442       2314855   
16   1108      幸福水泥        834345       3330601       2460423       1684246   
17   1109      信大水泥       1360434       6701130       4717018       2809557   
18   1110        東泥        417039       1676187       1176164        792194   
19   1201      味全公司       4540795      19436763      14509560       8828716   
20   1203      味王公司       1486287       6081031       4559801       2946087   
21   1210      大成長城      18186187      72442933      53361441      34984170   
22   1215      卜蜂企業       5035297      21235086      15807059      10220457   
23   1216        統一     107791643     431445520     330258558     214645776   
24   1217       愛之味        996828       4321819       3538841       1982512   
25   1218      泰山企業       1731205       7901670       6110590       3846852   
26   1219      福壽實業       2966586      11709984       8713846       5850333   
27   1220        台榮        612597       2747263       1945154       1203975   
28   1225       福懋油       2477770      11243509       8344865       5463107   
29   1227        佳格       7337166      27340587      19494272      12421997   
30   1229      聯華實業       1228699       5097818       3766018       2488302   
31   1231      聯華食品       2118070       8116880       5993552       3767881   
32   1232       大統益       4159273      16948746      12555938       8382090   
33   1233        天仁        562634       2193118       1649459       1086757   
34   1234        黑松       2145267       8901634       7003696       4454176   
35   1235        興泰          4696         57652         50030         13381   
36   1236      宏亞食品        499948       1972592       1410715        898907   
37   1256   鮮活果汁-KY        686855       3221239       2661941       1634338   
38   1262     綠悅-KY        907524       3859452       2967236       2137649   
39   1301        台塑      53012075     230370027     174017580     116643451   
40   1303      南亞塑膠      70920119     333061560     255361902     168674081   
41   1304        台聚      13493376      60892513      45648482      30332479   
42   1305        華夏       3227707      15192621      11298548       7822558   
43   1307      三芳化工       2628241       9492260       7067383       4457733   
44   1308        亞聚       1709711       6375134       4488953       2961396   
45   1309      台達化工       4600156      21683702      16585574      10788137   
46   1310        台苯       2937390      15382654      11981852       8076162   
47   1312      國喬石化       5005839      24741138      19019410      12291297   
48   1313        聯成      15365591      61258498      44029802      30044450   
49   1314       中石化       8138030      38503121      29

In [5]:
#Every single quarter data

#Each Dataframe object has a member variable shape i.e. a tuple that contains dimensions of a dataframe like,
#(Number_of_index, Number_of_columns)
#idx = df_revenue_sii.columns # the column index
#idx = df_revenue_sii.index # the row index
numOfRows_s = df_revenue_sii.shape[0] #len(df_revenue_sii) #len(df_revenue_sii.index)
numOfColumns_s = df_revenue_sii.shape[1] #len(df_revenue_sii.columns)
headNameOfColumns_s = df_revenue_sii.columns

print(numOfColumns_s)
df_revenue_sii

for row_index_s in range(0, numOfRows_s):
    for col_index_s in range(0, numOfColumns_s):
        #print(df_revenue_sii.columns.values[col_index].find('Q1')) # index of match string
        #print("Q1" in df_revenue_sii.columns.values[col_index]) # True OR False
        #How to Check if a Python String Contains Another String?
        if ("Q1" in df_revenue_sii.columns.values[col_index_s]): # if (df_revenue_sii.columns.values[col_index].find('Q1') > -1):
            continue
        else:
            if (u"公司代號" in df_revenue_sii.columns.values[col_index_s]):
                continue
            elif (u"公司名稱" in df_revenue_sii.columns.values[col_index_s]):
                continue
            elif (col_index_s == numOfColumns_s-1):
                continue
            else:
                df_revenue_sii.iloc[row_index_s, col_index_s] = float(df_revenue_sii.iloc[row_index_s, col_index_s]) - float(df_revenue_sii.iloc[row_index_s, col_index_s+1])

df_revenue_sii              

15


公司代號      公司名稱 Revenue_108Q1 Revenue_107Q4 Revenue_107Q3 Revenue_107Q2  \
0    2801      彰化銀行           NaN           NaN           NaN           NaN   
1    2809      京城銀行           NaN           NaN           NaN           NaN   
2    2812      台中銀行           NaN           NaN           NaN           NaN   
3    2820        華票           NaN           NaN           NaN           NaN   
4    2834      臺灣企銀           NaN           NaN           NaN           NaN   
5    2836        高銀           NaN           NaN           NaN           NaN   
6    2838      聯邦銀行           NaN           NaN           NaN           NaN   
7    2845      遠東商銀           NaN           NaN           NaN           NaN   
8    2849      安泰銀行           NaN           NaN           NaN           NaN   
9    2855      統一證券           NaN           NaN           NaN           NaN   
10   6005       群益證           NaN           NaN           NaN           NaN   
11   6024       群益期           NaN           NaN           NaN           NaN   
12   1101        台泥      25356328   3.49372e+07   3.21571e+07    3.3321e+07   
13   1102        亞泥      19385675   2.18329e+07    2.1899e+07   2.24352e+07   
14   1103        嘉泥        452376        597199        494280        529670   
15   1104      環球水泥       1187296   1.34455e+06   1.12159e+06   1.14876e+06   
16   1108      幸福水泥        834345        870178        776177        851540   
17   1109      信大水泥       1360434   1.98411e+06   1.90746e+06   1.74818e+06   
18   1110        東泥        417039        500023        383970        379704   
19   1201      味全公司       4540795    4.9272e+06   5.68084e+06   4.91137e+06   
20   1203      味王公司       1486287   1.52123e+06   1.61371e+06   1.49862e+06   
21   1210      大成長城      18186187   1.90815e+07   1.83773e+07   1.78611e+07   
22   1215      卜蜂企業       5035297   5.42803e+06    5.5866e+06   5.26322e+06   
23   1216        統一     107791643   1.01187e+08   1.15613e+08   1.10358e+08   
24   1217       愛之味        996828        782978   1.55633e+06        954079   
25   1218      泰山企業       1731205   1.79108e+06   2.26374e+06     2.002e+06   
26   1219      福壽實業       2966586   2.99614e+06   2.86351e+06   2.96962e+06   
27   1220        台榮        612597        802109        741179        630071   
28   1225       福懋油       2477770   2.89864e+06   2.88176e+06   2.66844e+06   
29   1227        佳格       7337166   7.84632e+06   7.07228e+06   5.00752e+06   
30   1229      聯華實業       1228699    1.3318e+06   1.27772e+06   1.26385e+06   
31   1231      聯華食品       2118070   2.12333e+06   2.22567e+06   1.75093e+06   
32   1232       大統益       4159273   4.39281e+06   4.17385e+06   4.26437e+06   
33   1233        天仁        562634        543659        562702        533317   
34   1234        黑松       2145267   1.89794e+06   2.54952e+06   2.13802e+06   
35   1235        興泰          4696          7622         36649          7348   
36   1236      宏亞食品        499948        561877        511808        327364   
37   1256   鮮活果汁-KY        686855        559298    1.0276e+06        934377   
38   1262     綠悅-KY        907524        892216        829587        861533   
39   1301        台塑      53012075   5.63524e+07   5.73741e+07   6.24761e+07   
40   1303      南亞塑膠      70920119   7.76997e+07   8.66878e+07   8.64541e+07   
41   1304        台聚      13493376    1.5244e+07    1.5316e+07   1.56623e+07   
42   1305        華夏       3227707   3.89407e+06   3.47599e+06   3.67836e+06   
43   1307      三芳化工       2628241   2.42488e+06   2.60965e+06   2.07237e+06   
44   1308        亞聚       1709711   1.88618e+06   1.52756e+06   1.63518e+06   
45   1309      台達化工       4600156   5.09813e+06   5.79744e+06   5.94597e+06   
46   1310        台苯       2937390    3.4008e+06   3.90569e+06   4.07172e+06   
47   1312      國喬石化       5005839   5.72173e+06   6.72811e+06   5.90459e+06   
48   1313        聯成      15365591   1.72287e+07   1.39854e+07   1.64749e+07   
49   1314       中石化       8138030   8.59237e+06   1.096

In [6]:
df_revenue_otc = generate_df_for_stocktype(g_year, g_season, g_how_many_year, 'otc', 'Revenue', u'營業收入', '綜合損益彙總表')

df_revenue_otc

C:\ProgramData\Anaconda2\lib\site-packages\ipykernel_launcher.py:34: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.



營業收入
('year:', 107)
('season:', 4)
營業收入
('year:', 107)
('season:', 3)
營業收入
('year:', 107)
('season:', 2)
營業收入
('year:', 107)
('season:', 1)
營業收入
('year:', 106)
('season:', 4)
營業收入
('year:', 106)
('season:', 3)
營業收入
('year:', 106)
('season:', 2)
營業收入
('year:', 106)
('season:', 1)
營業收入
('year:', 105)
('season:', 4)
營業收入
('year:', 105)
('season:', 3)
營業收入
('year:', 105)
('season:', 2)
營業收入
('year:', 105)
('season:', 1)


公司代號    公司名稱 Revenue_108Q1 Revenue_107Q4 Revenue_107Q3 Revenue_107Q2  \
0    6015    宏遠證券           NaN           NaN           NaN           NaN   
1    6016    康和證券           NaN           NaN           NaN           NaN   
2    6020     大展證           NaN           NaN           NaN           NaN   
3    6021     大慶證           NaN           NaN           NaN           NaN   
4    6023    元大期貨           NaN           NaN           NaN           NaN   
5    6026    福邦證券           NaN           NaN           NaN           NaN   
6    1258   其祥-KY        782591       2835038       2116036       1409658   
7    1259      安心       1302091       5252104       3945423       2543588   
8    1264      德麥        950178       3957774       2929325       1918781   
9    1333     恩得利         87432        393447        297986        204505   
10   1336      台翰        554401       2788241       2075040       1269314   
11   1565    精華光學       1623564       6675912       4968296       3305585   
12   1566      捷邦       1433378       5467490       4048513       2652481   
13   1569      濱川        905709       3566179       2560553       1638868   
14   1570    力肯實業        124503        642264        491355        303879   
15   1580    新麥企業        823691       4312015       3167040       2012693   
16   1584    精剛精密        178806        544205        421703        326104   
17   1586    和勤精機        430685       2453364       1907889       1253630   
18   1591   駿吉-KY        190197        840865        590951        357829   
19   1593      祺驊        187389        802061        580073        332117   
20   1595    川寶科技        290885       1756286       1351591        924822   
21   1597      直得        332331       2078901       1674386       1089719   
22   1599     宏佳騰        568602       2599350       2093925        974250   
23   1742      台蠟        264511        423811        290135        195230   
24   1752      南光        377094       1538527       1127917        769117   
25   1777      生泰        194560        784833        582086        395839   
26   1781    合世生醫        105853        617598        506462        305627   
27   1784    訊聯生技        186240        770607        557582        376298   
28   1785     光洋科       4753631      20887073      15846553      10219933   
29   1787     福盈科        440440       1930433       1423130        957092   
30   1788    杏昌生技        806251       3095154       2303453       1537640   
31   1795    美時製藥       2182671       6428894       4706299       3125066   
32   1799      易威         83724        419178        270574        175954   
33   1813     寶利徠        153038        459358        336857        214896   
34   1815    富喬工業       1144494       5051894       3781038       2378008   
35   2035    唐榮公司       3100883      14879535      12016395       8603295   
36   2061      風青        259400       1337846       1056897        728234   
37   2063      世鎧        251873       1089468        823967        520033   
38   2064      晉椿        528657       2741976       2068700       1368923   
39   2066      世德        653921       1974129       1291612        655138   
40   2067      嘉鋼        241905       1411788       1070828        716616   
41   2221    大甲永和        306768       1124784        843550        538555   
42   2230      泰茂        119484        565039        418164        274476   
43   2233      宇隆        629357       2549783       1969265       1341929   
44   2235      謚源        215144        781193        570317        361023   
45   2596    綠意開發          1067       1164271       1147719       1119772   
46   2640     大車隊        458189       1880286       1422953        944412   
47   2641    正德海運        194574        795087        589697        374353   
48   2643      捷迅        634756       2723361       1972798       1290706   
49   2718      晶悅         56614        219692        155091        101419   
50   2719     燦星旅        436065       2246001       1897820       1194742   
5

In [7]:
#Every single quarter data

#Each Dataframe object has a member variable shape i.e. a tuple that contains dimensions of a dataframe like,
#(Number_of_index, Number_of_columns)
#idx = df_revenue_otc.columns # the column index
#idx = df_revenue_otc.index # the row index
numOfRows_o = df_revenue_otc.shape[0] #len(df_revenue_otc) #len(df_revenue_otc.index)
numOfColumns_o = df_revenue_otc.shape[1] #len(df_revenue_otc.columns)
headNameOfColumns_o = df_revenue_otc.columns

print(numOfColumns_o)
df_revenue_otc

for row_index_o in range(0, numOfRows_o):
    for col_index_o in range(0, numOfColumns_o):
        #print(df_revenue_otc.columns.values[col_index].find('Q1')) # index of match string
        #print("Q1" in df_revenue_otc.columns.values[col_index]) # True OR False
        #How to Check if a Python String Contains Another String?
        if ("Q1" in df_revenue_otc.columns.values[col_index_o]): # if (df_revenue_otc.columns.values[col_index].find('Q1') > -1):
            continue
        else:
            if (u"公司代號" in df_revenue_otc.columns.values[col_index_o]):
                continue
            elif (u"公司名稱" in df_revenue_otc.columns.values[col_index_o]):
                continue
            elif (col_index_o == numOfColumns_o-1):
                continue
            else:
                df_revenue_otc.iloc[row_index_o, col_index_o] = float(df_revenue_otc.iloc[row_index_o, col_index_o]) - float(df_revenue_otc.iloc[row_index_o, col_index_o+1])

df_revenue_otc              

15


公司代號    公司名稱 Revenue_108Q1 Revenue_107Q4 Revenue_107Q3 Revenue_107Q2  \
0    6015    宏遠證券           NaN           NaN           NaN           NaN   
1    6016    康和證券           NaN           NaN           NaN           NaN   
2    6020     大展證           NaN           NaN           NaN           NaN   
3    6021     大慶證           NaN           NaN           NaN           NaN   
4    6023    元大期貨           NaN           NaN           NaN           NaN   
5    6026    福邦證券           NaN           NaN           NaN           NaN   
6    1258   其祥-KY        782591        719002        706378        731939   
7    1259      安心       1302091   1.30668e+06   1.40184e+06   1.30811e+06   
8    1264      德麥        950178   1.02845e+06   1.01054e+06        958837   
9    1333     恩得利         87432         95461         93481        101853   
10   1336      台翰        554401        713201        805726        666505   
11   1565    精華光學       1623564   1.70762e+06   1.66271e+06   1.72238e+06   
12   1566      捷邦       1433378   1.41898e+06   1.39603e+06   1.36259e+06   
13   1569      濱川        905709   1.00563e+06        921685        853635   
14   1570    力肯實業        124503        150909        187476        168407   
15   1580    新麥企業        823691   1.14498e+06   1.15435e+06   1.15864e+06   
16   1584    精剛精密        178806        122502         95599        134903   
17   1586    和勤精機        430685        545475        654259        650997   
18   1591   駿吉-KY        190197        249914        233122        202080   
19   1593      祺驊        187389        221988        247956        176249   
20   1595    川寶科技        290885        404695        426769        497475   
21   1597      直得        332331        404515        584667        584877   
22   1599     宏佳騰        568602        505425   1.11968e+06        618643   
23   1742      台蠟        264511        133676         94905        101623   
24   1752      南光        377094        410610        358800        390245   
25   1777      生泰        194560        202747        186247        204368   
26   1781    合世生醫        105853        111136        200835        216596   
27   1784    訊聯生技        186240        213025        181284        189328   
28   1785     光洋科       4753631   5.04052e+06   5.62662e+06   5.09357e+06   
29   1787     福盈科        440440        507303        466038        505136   
30   1788    杏昌生技        806251        791701        765813        766584   
31   1795    美時製藥       2182671    1.7226e+06   1.58123e+06   1.63528e+06   
32   1799      易威         83724        148604         94620         83758   
33   1813     寶利徠        153038        122501        121961        101842   
34   1815    富喬工業       1144494   1.27086e+06   1.40303e+06   1.22018e+06   
35   2035    唐榮公司       3100883   2.86314e+06    3.4131e+06   4.36394e+06   
36   2061      風青        259400        280949        328663        375941   
37   2063      世鎧        251873        265501        303934        277613   
38   2064      晉椿        528657        673276        699777        681323   
39   2066      世德        653921        682517        636474        341533   
40   2067      嘉鋼        241905        340960        354212        374539   
41   2221    大甲永和        306768        281234        304995        275909   
42   2230      泰茂        119484        146875        143688        144875   
43   2233      宇隆        629357        580518        627336        665821   
44   2235      謚源        215144        210876        209294        179784   
45   2596    綠意開發          1067         16552         27947        558305   
46   2640     大車隊        458189        457333        478541        480991   
47   2641    正德海運        194574        205390        215344        210717   
48   2643      捷迅        634756        750563        682092        669588   
49   2718      晶悅         56614         64601         53672         46609   
50   2719     燦星旅        436065        348181        703078        711567   
5

In [8]:
#Database-style DataFrame joining/merging: join, merge
#Concatenating objects: concat, append

#ignore_index = True 可以忽略合併時舊的 index 欄位，改採用自動產生的 index
df_revenue = pd.concat([df_revenue_sii,df_revenue_otc],axis=0, ignore_index=True)

df_revenue

公司代號      公司名稱 Revenue_108Q1 Revenue_107Q4 Revenue_107Q3 Revenue_107Q2  \
0     2801      彰化銀行           NaN           NaN           NaN           NaN   
1     2809      京城銀行           NaN           NaN           NaN           NaN   
2     2812      台中銀行           NaN           NaN           NaN           NaN   
3     2820        華票           NaN           NaN           NaN           NaN   
4     2834      臺灣企銀           NaN           NaN           NaN           NaN   
5     2836        高銀           NaN           NaN           NaN           NaN   
6     2838      聯邦銀行           NaN           NaN           NaN           NaN   
7     2845      遠東商銀           NaN           NaN           NaN           NaN   
8     2849      安泰銀行           NaN           NaN           NaN           NaN   
9     2855      統一證券           NaN           NaN           NaN           NaN   
10    6005       群益證           NaN           NaN           NaN           NaN   
11    6024       群益期           NaN           NaN           NaN           NaN   
12    1101        台泥      25356328   3.49372e+07   3.21571e+07    3.3321e+07   
13    1102        亞泥      19385675   2.18329e+07    2.1899e+07   2.24352e+07   
14    1103        嘉泥        452376        597199        494280        529670   
15    1104      環球水泥       1187296   1.34455e+06   1.12159e+06   1.14876e+06   
16    1108      幸福水泥        834345        870178        776177        851540   
17    1109      信大水泥       1360434   1.98411e+06   1.90746e+06   1.74818e+06   
18    1110        東泥        417039        500023        383970        379704   
19    1201      味全公司       4540795    4.9272e+06   5.68084e+06   4.91137e+06   
20    1203      味王公司       1486287   1.52123e+06   1.61371e+06   1.49862e+06   
21    1210      大成長城      18186187   1.90815e+07   1.83773e+07   1.78611e+07   
22    1215      卜蜂企業       5035297   5.42803e+06    5.5866e+06   5.26322e+06   
23    1216        統一     107791643   1.01187e+08   1.15613e+08   1.10358e+08   
24    1217       愛之味        996828        782978   1.55633e+06        954079   
25    1218      泰山企業       1731205   1.79108e+06   2.26374e+06     2.002e+06   
26    1219      福壽實業       2966586   2.99614e+06   2.86351e+06   2.96962e+06   
27    1220        台榮        612597        802109        741179        630071   
28    1225       福懋油       2477770   2.89864e+06   2.88176e+06   2.66844e+06   
29    1227        佳格       7337166   7.84632e+06   7.07228e+06   5.00752e+06   
30    1229      聯華實業       1228699    1.3318e+06   1.27772e+06   1.26385e+06   
31    1231      聯華食品       2118070   2.12333e+06   2.22567e+06   1.75093e+06   
32    1232       大統益       4159273   4.39281e+06   4.17385e+06   4.26437e+06   
33    1233        天仁        562634        543659        562702        533317   
34    1234        黑松       2145267   1.89794e+06   2.54952e+06   2.13802e+06   
35    1235        興泰          4696          7622         36649          7348   
36    1236      宏亞食品        499948        561877        511808        327364   
37    1256   鮮活果汁-KY        686855        559298    1.0276e+06        934377   
38    1262     綠悅-KY        907524        892216        829587        861533   
39    1301        台塑      53012075   5.63524e+07   5.73741e+07   6.24761e+07   
40    1303      南亞塑膠      70920119   7.76997e+07   8.66878e+07   8.64541e+07   
41    1304        台聚      13493376    1.5244e+07    1.5316e+07   1.56623e+07   
42    1305        華夏       3227707   3.89407e+06   3.47599e+06   3.67836e+06   
43    1307      三芳化工       2628241   2.42488e+06   2.60965e+06   2.07237e+06   
44    1308        亞聚       1709711   1.88618e+06   1.52756e+06   1.63518e+06   
45    1309      台達化工       4600156   5.09813e+06   5.79744e+06   5.94597e+06   
46    1310        台苯       2937390    3.4008e+06   3.90569e+06   4.07172e+06   
47    1312      國喬石化       5005839   5.72173e+06   6.72811e+06   5.90459e+06   
48    1313        聯成      15365591   1.72287e+07   1.39854e+07   1.64749e+07   
49    

In [9]:
#檢查column資料型態

#df_revenue.info() #non-null object
#df_revenue.dtypes #object
#df_revenue.applymap(np.isreal) #all False
'''
公司代號              int64
公司名稱             object
Revenue(%)_107Q1    float64
Revenue(%)_106Q4    float64
Revenue(%)_106Q3    float64
Revenue(%)_106Q2    float64
Revenue(%)_106Q1    float64
Revenue(%)_105Q4    float64
Revenue(%)_105Q3    float64
Revenue(%)_105Q2    float64
Revenue(%)_105Q1    float64
Revenue(%)_104Q4    float64
Revenue(%)_104Q3    float64
Revenue(%)_104Q2    float64
Revenue(%)_104Q1    float64
dtype: object
'''

df_revenue = df_revenue.convert_objects(convert_numeric=True) #轉成float型態方便後續處理

df_revenue.convert_objects(convert_numeric=True).dtypes #轉成float型態方便後續處理

C:\ProgramData\Anaconda2\lib\site-packages\ipykernel_launcher.py:25: FutureWarning: convert_objects is deprecated.  To re-infer data dtypes for object columns, use DataFrame.infer_objects()
For all other conversions use the data-type specific converters pd.to_datetime, pd.to_timedelta and pd.to_numeric.
C:\ProgramData\Anaconda2\lib\site-packages\ipykernel_launcher.py:27: FutureWarning: convert_objects is deprecated.  To re-infer data dtypes for object columns, use DataFrame.infer_objects()
For all other conversions use the data-type specific converters pd.to_datetime, pd.to_timedelta and pd.to_numeric.


公司代號               int64
公司名稱              object
Revenue_108Q1    float64
Revenue_107Q4    float64
Revenue_107Q3    float64
Revenue_107Q2    float64
Revenue_107Q1    float64
Revenue_106Q4    float64
Revenue_106Q3    float64
Revenue_106Q2    float64
Revenue_106Q1    float64
Revenue_105Q4    float64
Revenue_105Q3    float64
Revenue_105Q2    float64
Revenue_105Q1    float64
dtype: object

In [10]:
def isFloat(element):  
    try:
        float(element)
        return True
    except ValueError:
        return False

In [11]:
def growth_func(row, year, season):
    previous_year = year - 1
    #判斷是否為文字而非數字
    if(isFloat(row['Revenue_{0}Q{1}'.format(year, season)]) == True):
        subsequent_value = float(row['Revenue_{0}Q{1}'.format(year, season)])
        previous_value = float(row['Revenue_{0}Q{1}'.format(previous_year, season)])
   
        if(previous_value == 0):
            result = ((subsequent_value - previous_value)/np.abs(subsequent_value))*100
        else:
            result = ((subsequent_value - previous_value)/np.abs(previous_value))*100            
        return float("{0:.2f}".format(result)) # Limiting floats to two decimal points
     
    else:
        return 'NoValue'

In [12]:
def ma2q_growth_func(row, year, season):
    #判斷是否為文字而非數字
    if(isFloat(row['Revenue_{0}Q{1}'.format(year, season)]) == True):
        previous_value = float(row['Growth_{0}Q{1}'.format(year, season)])
        if (season != 1):
            season = season - 1
        else:
            season = 4
            year = year - 1
        subsequent_value = float(row['Growth_{0}Q{1}'.format(year, season)])
        
        result = ((subsequent_value + previous_value)/2)
        return float("{0:.2f}".format(result)) # Limiting floats to two decimal points
    
    else:
        return 'NoValue'

In [13]:
# use the apply function in pandas to apply the function
# Note the axis=1 specifier, that means that the application is done at a row, rather than a column level
# df_eps.apply (lambda row: growth_func (row),axis=1)

year = g_year
season = g_season
howmany_year_data = g_how_many_year

#first 4 quarter don't need to be calculated growth
for i in range(int(howmany_year_data*4-4)):
    df_revenue['Growth_{0}Q{1}'.format(year, season)] = df_revenue.apply (lambda row: growth_func(row, year, season),axis=1)
    if (season != 1):
        season = season - 1
    else:
        season = 4
        year = year - 1

C:\ProgramData\Anaconda2\lib\site-packages\ipykernel_launcher.py:9: RuntimeWarning: invalid value encountered in double_scalars
  if __name__ == '__main__':


In [14]:
# use the apply function in pandas to apply the function
# Note the axis=1 specifier, that means that the application is done at a row, rather than a column level
# df_eps.apply (lambda row: growth_func (row),axis=1)

year = g_year
season = g_season
howmany_year_data = g_how_many_year

#first 4 quarter don't need to be calculated growth
for i in range(int(howmany_year_data*4-4-1)):
    df_revenue['2QMAGrowth_{0}Q{1}'.format(year, season)] = df_revenue.apply (lambda row: ma2q_growth_func(row, year, season),axis=1)
    if (season != 1):
        season = season - 1
    else:
        season = 4
        year = year - 1

In [15]:
def get_basic_info_for_ftock(stocktype):

    #get basic info of company
    '''
    抓取上市櫃股票的代號、名稱...等資料。
    上市
    http://isin.twse.com.tw/isin/C_public.jsp?strMode=2
    上櫃
    http://isin.twse.com.tw/isin/C_public.jsp?strMode=4
    '''
    #http://bloggerkaiweng.blogspot.com/2016/09/python.html

    if(stocktype == 'sii'):
        url='http://isin.twse.com.tw/isin/C_public.jsp?strMode=2'
    else:
        url='http://isin.twse.com.tw/isin/C_public.jsp?strMode=4'
    
    r = requests.get(url, stream=True)#, verify=False, proxies=proxyDict)
    r.encoding = 'big5hkscs' 
    dfshow = pd.read_html(r.text)

    for i, df in enumerate(dfshow):
        df.columns = df.iloc[0]
        dfshow[i] = df.iloc[1:]

    df = pd.concat(dfshow).applymap(lambda x: x if x != '--' else np.nan)
    df = df[df[u'有價證券代號及名稱'] != u'股票']
    df = df[~df[u'有價證券代號及名稱'].isnull()]
    df = df.reset_index(drop=True)
    
    newdf=df[df[u'產業別'] > '0']
    del newdf[u'國際證券辨識號碼(ISIN Code)'],newdf['CFICode'],newdf[u'備註']

    df2=newdf[u'有價證券代號及名稱'].str.split(u' ', expand=True)
    df2 = df2.reset_index(drop=True)
    newdf = newdf.reset_index(drop=True)
    for i in df2.index:
        if u'　' in df2.iat[i,0]:
            df2.iat[i,1]=df2.iat[i,0].split(u'　')[1]
            df2.iat[i,0]=df2.iat[i,0].split(u'　')[0]
    newdf=df2.join(newdf)
    newdf=newdf.rename(columns = {0:u'公司代號',1:u'股票名稱'})
    del newdf[u'有價證券代號及名稱']

    return newdf

In [16]:
df_basicinfo_sii = get_basic_info_for_ftock('sii').convert_objects(convert_numeric=True) #轉成float型態
df_basicinfo_otc = get_basic_info_for_ftock('otc').convert_objects(convert_numeric=True) #轉成float型態

df_basicinfo = pd.concat([df_basicinfo_sii,df_basicinfo_otc],axis=0, ignore_index=True)
#df_eps_basicinfo_sii.dtypes
#df_eps_basicinfo_otc

df_revenue = df_revenue.merge(df_basicinfo, on=u'公司代號', how='inner')

df_revenue

C:\ProgramData\Anaconda2\lib\site-packages\ipykernel_launcher.py:1: FutureWarning: convert_objects is deprecated.  To re-infer data dtypes for object columns, use DataFrame.infer_objects()
For all other conversions use the data-type specific converters pd.to_datetime, pd.to_timedelta and pd.to_numeric.
  """Entry point for launching an IPython kernel.
C:\ProgramData\Anaconda2\lib\site-packages\ipykernel_launcher.py:2: FutureWarning: convert_objects is deprecated.  To re-infer data dtypes for object columns, use DataFrame.infer_objects()
For all other conversions use the data-type specific converters pd.to_datetime, pd.to_timedelta and pd.to_numeric.
  


公司代號      公司名稱  Revenue_108Q1  Revenue_107Q4  Revenue_107Q3  \
0     2801      彰化銀行            NaN            NaN            NaN   
1     2809      京城銀行            NaN            NaN            NaN   
2     2812      台中銀行            NaN            NaN            NaN   
3     2820        華票            NaN            NaN            NaN   
4     2834      臺灣企銀            NaN            NaN            NaN   
5     2836        高銀            NaN            NaN            NaN   
6     2838      聯邦銀行            NaN            NaN            NaN   
7     2845      遠東商銀            NaN            NaN            NaN   
8     2849      安泰銀行            NaN            NaN            NaN   
9     2855      統一證券            NaN            NaN            NaN   
10    6005       群益證            NaN            NaN            NaN   
11    6024       群益期            NaN            NaN            NaN   
12    1101        台泥   2.535633e+07   3.493725e+07   3.215711e+07   
13    1102        亞泥   1.938568e+07   2.183294e+07   2.189898e+07   
14    1103        嘉泥   4.523760e+05   5.971990e+05   4.942800e+05   
15    1104      環球水泥   1.187296e+06   1.344552e+06   1.121587e+06   
16    1108      幸福水泥   8.343450e+05   8.701780e+05   7.761770e+05   
17    1109      信大水泥   1.360434e+06   1.984112e+06   1.907461e+06   
18    1110        東泥   4.170390e+05   5.000230e+05   3.839700e+05   
19    1201      味全公司   4.540795e+06   4.927203e+06   5.680844e+06   
20    1203      味王公司   1.486287e+06   1.521230e+06   1.613714e+06   
21    1210      大成長城   1.818619e+07   1.908149e+07   1.837727e+07   
22    1215      卜蜂企業   5.035297e+06   5.428027e+06   5.586602e+06   
23    1216        統一   1.077916e+08   1.011870e+08   1.156128e+08   
24    1217       愛之味   9.968280e+05   7.829780e+05   1.556329e+06   
25    1218      泰山企業   1.731205e+06   1.791080e+06   2.263738e+06   
26    1219      福壽實業   2.966586e+06   2.996138e+06   2.863513e+06   
27    1220        台榮   6.125970e+05   8.021090e+05   7.411790e+05   
28    1225       福懋油   2.477770e+06   2.898644e+06   2.881758e+06   
29    1227        佳格   7.337166e+06   7.846315e+06   7.072275e+06   
30    1229      聯華實業   1.228699e+06   1.331800e+06   1.277716e+06   
31    1231      聯華食品   2.118070e+06   2.123328e+06   2.225671e+06   
32    1232       大統益   4.159273e+06   4.392808e+06   4.173848e+06   
33    1233        天仁   5.626340e+05   5.436590e+05   5.627020e+05   
34    1234        黑松   2.145267e+06   1.897938e+06   2.549520e+06   
35    1235        興泰   4.696000e+03   7.622000e+03   3.664900e+04   
36    1236      宏亞食品   4.999480e+05   5.618770e+05   5.118080e+05   
37    1256   鮮活果汁-KY   6.868550e+05   5.592980e+05   1.027603e+06   
38    1262     綠悅-KY   9.075240e+05   8.922160e+05   8.295870e+05   
39    1301        台塑   5.301208e+07   5.635245e+07   5.737413e+07   
40    1303      南亞塑膠   7.092012e+07   7.769966e+07   8.668782e+07   
41    1304        台聚   1.349338e+07   1.524403e+07   1.531600e+07   
42    1305        華夏   3.227707e+06   3.894073e+06   3.475990e+06   
43    1307      三芳化工   2.628241e+06   2.424877e+06   2.609650e+06   
44    1308        亞聚   1.709711e+06   1.886181e+06   1.527557e+06   
45    1309      台達化工   4.600156e+06   5.098128e+06   5.797437e+06   
46    1310        台苯   2.937390e+06   3.400802e+06   3.905690e+06   
47    1312      國喬石化   5.005839e+06   5.721728e+06   6.728113e+06   
48    1313        聯成   1.536559e+07   1.722870e+07   1.398535e+07   
49    1314       中石化   8.138030e+06   8.592366e+06   1.096832e+07   
50    1315      達新工業   5.105190e+05   6.416450e+05   7.263180e+05   
51    1316        上曜   1.341770e+05   1.416350e+05   1.960620e+05   
52    1319        東陽   5.309893e+06   5.560604e+06   5.394502e+06   
53    1321        大洋   1.030509e+06   1.233524e+06   1.096609e+06   
54    1323        永裕   8.448070e+05   9.738530e+05   9.758040e+05   
55    1324      地球工業   2.909390e+05   2.900040e+05   2.798750e+05   
56    1325        恒大   1.956530e+05   2.511100e+05   2.162020e+05   
57  

In [17]:
# pandas styling
def color_white(val):
    """
    Takes a scalar and returns a string with
    the css property `'color: red'` for negative
    strings, black otherwise.
    """
    color = 'white'
    return 'color: %s' % color

def background_color(val):    
    if float(val) < 0:
        backgroundcolor = '#ff0000'
    elif float(val) < 10:
        backgroundcolor = '#f47721'
    elif float(val) < 20:
        backgroundcolor = '#ffdd00'
    elif float(val) < 30:
        backgroundcolor = '#5ecc62'
    else:
        backgroundcolor = '#00ad45'
    return 'background-color: %s' % backgroundcolor

"""
Export to Excel
Some support is available for exporting styled DataFrames to Excel worksheets using the OpenPyXL or XlsxWriter engines. 
CSS2.2 properties handled include:

* background-color
* border-style, border-width, border-color and their {top, right, bottom, left variants}
* color
* font-family
* font-style
* font-weight
* text-align
* text-decoration
* vertical-align
* white-space: nowrap
"""
def font_family(val):    
    fontfamily = 'Calibri'
    return 'font-family: %s' % fontfamily

def font_size(val):    
    fontsize = '10pt'
    return 'font-size: %s' % fontsize

In [18]:
# styled dataframe can use .to_excel('Styled_Basic_EPS.xlsx', engine='openpyxl') to export excel with style
year = g_year
season = g_season
howmany_year_data = g_how_many_year

#first 4 quarter don't need to be calculated growth
columns_name = []
for i in range(int(howmany_year_data*4-4)):
    columns_name.append('Growth_{0}Q{1}'.format(year, season))
    columns_name.append('2QMAGrowth_{0}Q{1}'.format(year, season))
    if (season != 1):
        season = season - 1
    else:
        season = 4
        year = year - 1

print(columns_name)

# the cell’s style depends only on it’s own value. That means we should use the Styler.applymap method which works elementwise.
# Now suppose you wanted to highlight the maximum value in each column. We can’t use .applymap anymore since that operated elementwise. Instead, we’ll turn to .apply which operates columnwise (or rowwise using the axis keyword).
#df_eps.style.applymap(color_negative_red, subset=pd.IndexSlice[:, ['Growth_107Q1','Growth_106Q4','Growth_106Q3','Growth_106Q2','Growth_106Q1','Growth_105Q4','Growth_105Q3','Growth_105Q2']]).applymap(background_color, subset=pd.IndexSlice[:, ['Growth_107Q1','Growth_106Q4','Growth_106Q3','Growth_106Q2','Growth_106Q1','Growth_105Q4','Growth_105Q3','Growth_105Q2']]).to_excel('Styled_Basic_EPS.xlsx', 'EPS_Basic', engine='openpyxl')
df_revenue.style.applymap(color_white, subset=pd.IndexSlice[:, columns_name]).applymap(background_color, subset=pd.IndexSlice[:, columns_name]).applymap(font_family).applymap(font_size).to_excel('Styled_Basic_Perspective_Revenue.xlsx', 'Revenue_Basic', engine='openpyxl')

# Pandas style function to hignlight specific columns
# http://pandas.pydata.org/pandas-docs/stable/style.html#Finer-Control:-Slicing
# Finer Control: Slicing
# ex: df.style.apply(highlight_max, subset=['B', 'C', 'D'])

['Growth_108Q1', '2QMAGrowth_108Q1', 'Growth_107Q4', '2QMAGrowth_107Q4', 'Growth_107Q3', '2QMAGrowth_107Q3', 'Growth_107Q2', '2QMAGrowth_107Q2', 'Growth_107Q1', '2QMAGrowth_107Q1', 'Growth_106Q4', '2QMAGrowth_106Q4', 'Growth_106Q3', '2QMAGrowth_106Q3', 'Growth_106Q2', '2QMAGrowth_106Q2']


C:\ProgramData\Anaconda2\lib\site-packages\pandas\core\indexing.py:1472: FutureWarning: 
Passing list-likes to .loc or [] with any missing label will raise
KeyError in the future, you can use .reindex() as an alternative.

See the documentation here:
https://pandas.pydata.org/pandas-docs/stable/indexing.html#deprecate-loc-reindex-listlike
  return self._getitem_tuple(key)
